<a href="https://colab.research.google.com/github/nxxk23/PROJECT/blob/main/CompareImputation.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
!pip install missingpy
!pip install scikit-learn==1.1.2

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49.1/49.1 kB 871.6 kB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 30.5/30.5 MB 18.1 MB/s eta 0:00:00
  Attempting uninstall: scikit-learn
    Found existing installation: scikit-learn 1.2.2
    Uninstalling scikit-learn-1.2.2:
      Successfully uninstalled scikit-learn-1.2.2
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
bigframes 0.17.0 requires scikit-learn>=1.2.2, but you have scikit-learn 1.1.2 which is incompatible.


In [ ]:
import sklearn
print(sklearn.__version__)

1.1.2


In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


**OriginalData**

In [ ]:
import pandas as pd
widetable = pd.read_excel('/content/drive/MyDrive/ckdresearch2023/Assign/Wide Table/WideTable.xlsx')
widetable = widetable.iloc[:, 1:]
widetable.head()

PatientUID  PatientVisitUID     Slopes  G1M2:ARB  G3M1:Statin  G5M2:NSAIDs  \
0        2299          3386255  -7.158596        90            0            0   
1        2299          4546471   5.550691        90           90            0   
2        2299          5812902  -6.063710       100          100           34   
3        2299          6947220 -12.812245        35            0            1   
4        2299          8186767  28.287500       100            0           15   

   G1M5:Diuretic  G1M7:Beta blocker  G1M3:Dihydropyridine CCB  G1M6:MRA  ...  \
0              0                  0                         0         0  ...   
1              0                  0                         0         0  ...   
2              0                  0                         0         0  ...   
3             35                  0                         0         0  ...   
4              0                  0                         0         0  ...   

   L20:HbA1c  L21:Cholesterol  L22:Triglyceride  L23:LDL Cholesterol  \
0        NaN            215.0              81.0                123.0   
1        NaN            219.0              64.0                146.0   
2        5.3            193.0              62.0                129.0   
3        NaN            205.0              69.0                139.0   
4        5.5            198.0              74.0                129.0   

   L24:HDL Cholesterol  L28:UrineProtein/Cr ratio  eGFR_t1  \
0                 99.0                        NaN    63.60   
1                 73.0                        NaN    70.20   
2                 65.0                        NaN    64.02   
3                 76.0                        NaN    48.54   
4                 60.0                        NaN    80.47   

                  time_t1                      LabLocation  \
0 2017-10-03 09:19:54.710  ห้องปฏิบัติการจุลทรรศน์วินิจฉัย   
1 2018-12-12 09:18:49.913  ห้องปฏิบัติการจุลทรรศน์วินิจฉัย   
2 2019-12-19 09:51:24.427  ห้องปฏิบัติการจุลทรรศน์วินิจฉัย   
3 2021-03-04 10:01:42.113  ห้องปฏิบัติการจุลทรรศน์วินิจฉัย   
4 2022-04-21 08:45:54.580  ห้องปฏิบัติการจุลทรรศน์วินิจฉัย   

                  LabCwhen  
0  2559-08-15 09:51:55.203  
1  2560-10-03 09:19:54.920  
2  2561-12-12 10:15:36.930  
3  2562-12-19 09:51:24.577  
4  2564-03-04 10:07:37.037  

[5 rows x 82 columns]

In [ ]:
df = widetable.copy()

**dummy**

In [ ]:
widetable['Sex'] = widetable['Sex'].replace({'ชาย': 0, 'หญิง': 1})

In [ ]:
nationality_map = {'ไทย': 0}

caucasian = ['บริติช  (อังกฤษ, สก็อตแลนด์)', 'อเมริกัน', 'เยอรมัน', 'โอมาน', 'ออสเตรเลีย', 'แคนาดา',
             'อิตาลี', 'สวิส', 'ซีเรีย', 'เดนมาร์ก', 'นอร์เวย์', 'ดัตช์', 'สเปน', 'เบลเยียม', 'ไอซ์แลนด์',
             'ฝรั่งเศส', 'เซนต์คิตส์และเนวิส', 'สวีเดน', 'ออสเตรีย', 'ไซปรัส']
asian = ['ลาว','จีน','เวียดนาม','เขมรอพยพ','ไทยลื้อ','ญี่ปุ่น', 'จีน(ไต้หวัน)']
other = ['ไม่ระบุ','อื่นๆ','ไร้สัญชาติ']

for nationality in asian:
    nationality_map[nationality] = 1

for nationality in caucasian:
    nationality_map[nationality] = 2

for nationality in other:
    nationality_map[nationality] = 3

widetable['NATNL'] = widetable['NATNL'].replace(nationality_map)

In [ ]:
import numpy as np

In [ ]:
widetable['LabLocation'] = np.where(widetable['LabLocation'] == "ห้องปฏิบัติการจุลทรรศน์วินิจฉัย", 1, 0)

In [ ]:
df_no_missing = widetable.dropna()
df_no_missing= df_no_missing.reset_index(drop=True)
df_no_missing.shape

(148, 82)

In [ ]:
remove = ['Slopes', 'PatientUID', 'PatientVisitUID','InPatient', 'OutPatient', 'Emergency','eGFR_t1','time_t1', 'VisitLocation', 'StartDTTM','EndDttm', 'LabCwhen']
df_no_missing = df_no_missing.drop(columns=remove)
no_missing = df_no_missing.copy()

In [ ]:
import pandas as pd
import numpy as np
from sklearn.experimental import enable_iterative_imputer
from sklearn.impute import IterativeImputer
from sklearn.metrics import mean_squared_error, mean_absolute_error
import matplotlib.pyplot as plt
from scipy import stats
import sklearn.neighbors._base
import sys
sys.modules['sklearn.neighbors.base'] = sklearn.neighbors._base
from missingpy import MissForest

**สุ่มค่าว่างในข้อมูล**

In [ ]:
missing_percentage = widetable.isnull().mean()
missing_probabilities = missing_percentage / missing_percentage.sum()

In [ ]:
import numpy as np
df_with_missing = no_missing.copy()
for column in df_with_missing.columns:
    num_missing = int(np.round(missing_percentage[column] * len(df_with_missing)))
    missing_indices = np.random.choice(len(df_with_missing), num_missing, replace=False)
    df_with_missing.loc[missing_indices, column] = np.nan


In [ ]:
df_with_missing.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 148 entries, 0 to 147
Data columns (total 70 columns):
 #   Column                        Non-Null Count  Dtype  
---  ------                        --------------  -----  
 0   G1M2:ARB                      148 non-null    float64
 1   G3M1:Statin                   148 non-null    float64
 2   G5M2:NSAIDs                   148 non-null    float64
 3   G1M5:Diuretic                 148 non-null    float64
 4   G1M7:Beta blocker             148 non-null    float64
 5   G1M3:Dihydropyridine CCB      148 non-null    float64
 6   G1M6:MRA                      148 non-null    float64
 7   G1M1:ACEI                     148 non-null    float64
 8   G2M2:Metformin                148 non-null    float64
 9   G2M3:DPP4 inhibitor           148 non-null    float64
 10  G2M1:SU                       148 non-null    float64
 11  G3M3:Fibrate                  148 non-null    float64
 12  G2M5:SGLT2i                   148 non-null    float64
 13  G4M1:

In [ ]:
num_iterations = 50

mse_Mice = []
mape_Mice = []
mae_Mice = []

for _ in range(num_iterations):
    random_missing_indices = {}
    for column in df_with_missing.columns:
        num_missing = int(np.round(missing_probabilities[column] * len(df_with_missing)))
        random_missing_indices[column] = np.random.choice(len(df_with_missing), num_missing, replace=False)

    imputer_mice = IterativeImputer(random_state=0, initial_strategy='median')
    data_mice = df_with_missing.copy()
    for column in df_with_missing.columns:
        data_mice.loc[random_missing_indices[column], column] = np.nan

    data_mice_filled = imputer_mice.fit_transform(data_mice)
    Mice = pd.DataFrame(data_mice_filled, columns=data_mice.columns).round(1)

    # Calculate and append results for MICE
    mse_Mice.append(mean_squared_error(no_missing, Mice))
    true_values_mice = no_missing.values.flatten()
    imputed_values_mice = Mice.values.flatten()

    non_zero_mask_mice = true_values_mice != 0
    true_values_non_zero_mice = true_values_mice[non_zero_mask_mice]
    imputed_values_non_zero_mice = imputed_values_mice[non_zero_mask_mice]

    mape_Mice.append(np.mean(np.abs((true_values_non_zero_mice - imputed_values_non_zero_mice) / true_values_non_zero_mice)) * 100)
    mae_Mice.append(mean_absolute_error(no_missing, Mice))

/usr/local/lib/python3.10/dist-packages/sklearn/impute/_iterative.py:713: ConvergenceWarning: [IterativeImputer] Early stopping criterion not reached.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/impute/_iterative.py:713: ConvergenceWarning: [IterativeImputer] Early stopping criterion not reached.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/impute/_iterative.py:713: ConvergenceWarning: [IterativeImputer] Early stopping criterion not reached.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/impute/_iterative.py:713: ConvergenceWarning: [IterativeImputer] Early stopping criterion not reached.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/impute/_iterative.py:713: ConvergenceWarning: [IterativeImputer] Early stopping criterion not reached.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/impute/_iterative.py:713: ConvergenceWarning: [IterativeImputer] Early stopping criterion not reached.
  warning

In [ ]:
mae_Mice

[2.9190521235521234,
 3.112015444015444,
 3.0742818532818537,
 3.0616023166023165,
 3.2092490347490346,
 2.9384980694980696,
 3.076295366795367,
 3.0944652509652513,
 3.015164092664093,
 3.0760752895752894,
 3.127471042471043,
 3.0312567567567568,
 2.9993667953667957,
 2.9264826254826257,
 3.0528629343629348,
 3.0131023166023163,
 3.1395135135135135,
 2.9717548262548257,
 3.198133204633205,
 3.0286389961389966,
 3.1174343629343633,
 2.940102316602317,
 2.958772200772201,
 3.0158416988416987,
 2.9159942084942085,
 3.0785444015444017,
 3.023828185328185,
 2.97919305019305,
 3.036517374517375,
 3.02584555984556,
 3.0749498069498062,
 3.0146389961389963,
 2.990453667953668,
 2.939625482625482,
 3.0289710424710425,
 2.9840617760617762,
 3.0156718146718147,
 2.985260617760618,
 3.0280212355212353,
 3.1124942084942084,
 3.070942084942085,
 3.0388880308880304,
 3.1056428571428567,
 3.014816602316602,
 3.171440154440155,
 2.8854247104247106,
 3.222249034749034,
 3.186870656370656,
 3.0479864864

In [ ]:
num_iterations = 50

mse_MF = []
mape_MF = []
mae_MF = []

for _ in range(num_iterations):
    random_missing_indices = {}
    for column in df_with_missing.columns:
        num_missing = int(np.round(missing_probabilities[column] * len(df_with_missing)))
        random_missing_indices[column] = np.random.choice(len(df_with_missing), num_missing, replace=False)

    imputer_missforest = MissForest(random_state=0, verbose=1)
    data_mf = df_with_missing.copy()
    for column in df_with_missing.columns:
        data_mf.loc[random_missing_indices[column], column] = np.nan

    data_mf_filled = imputer_missforest.fit_transform(data_mf)
    MF = pd.DataFrame(data_mf_filled, columns=data_mf.columns).round(1)

    # Calculate and append results for MF
    mse_MF.append(mean_squared_error(no_missing, MF))
    true_values_mf = no_missing.values.flatten()
    imputed_values_mf = MF.values.flatten()

    non_zero_mask_mf = true_values_mf != 0
    true_values_non_zero_mf = true_values_mf[non_zero_mask_mf]
    imputed_values_non_zero_mf = imputed_values_mf[non_zero_mask_mf]

    mape_MF.append(np.mean(np.abs((true_values_non_zero_mf - imputed_values_non_zero_mf) / true_values_non_zero_mf)) * 100)
    mae_MF.append(mean_absolute_error(no_missing, MF))

/usr/local/lib/python3.10/dist-packages/sklearn/ensemble/_forest.py:400: FutureWarning: Criterion 'mse' was deprecated in v1.0 and will be removed in version 1.2. Use `criterion='squared_error'` which is equivalent.
  warn(
/usr/local/lib/python3.10/dist-packages/sklearn/ensemble/_forest.py:416: FutureWarning: `max_features='auto'` has been deprecated in 1.1 and will be removed in 1.3. To keep the past behaviour, explicitly set `max_features=1.0` or remove this parameter as it is also the default value for RandomForestRegressors and ExtraTreesRegressors.
  warn(
[Parallel(n_jobs=-1)]: Using backend ThreadingBackend with 2 concurrent workers.
[Parallel(n_jobs=-1)]: Done  46 tasks      | elapsed:    0.1s
[Parallel(n_jobs=-1)]: Done 100 out of 100 | elapsed:    0.2s finished
[Parallel(n_jobs=2)]: Using backend ThreadingBackend with 2 concurrent workers.
[Parallel(n_jobs=2)]: Done  46 tasks      | elapsed:    0.0s
[Parallel(n_jobs=2)]: Done 100 out of 100 | elapsed:    0.0s finished
/usr/l

Iteration: 0


[Parallel(n_jobs=-1)]: Done  46 tasks      | elapsed:    0.2s
[Parallel(n_jobs=-1)]: Done 100 out of 100 | elapsed:    0.4s finished
[Parallel(n_jobs=2)]: Using backend ThreadingBackend with 2 concurrent workers.
[Parallel(n_jobs=2)]: Done  46 tasks      | elapsed:    0.0s
[Parallel(n_jobs=2)]: Done 100 out of 100 | elapsed:    0.0s finished
/usr/local/lib/python3.10/dist-packages/sklearn/ensemble/_forest.py:400: FutureWarning: Criterion 'mse' was deprecated in v1.0 and will be removed in version 1.2. Use `criterion='squared_error'` which is equivalent.
  warn(
/usr/local/lib/python3.10/dist-packages/sklearn/ensemble/_forest.py:416: FutureWarning: `max_features='auto'` has been deprecated in 1.1 and will be removed in 1.3. To keep the past behaviour, explicitly set `max_features=1.0` or remove this parameter as it is also the default value for RandomForestRegressors and ExtraTreesRegressors.
  warn(
[Parallel(n_jobs=-1)]: Using backend ThreadingBackend with 2 concurrent workers.
[Paral

Iteration: 1


[Parallel(n_jobs=-1)]: Done 100 out of 100 | elapsed:    0.2s finished
[Parallel(n_jobs=2)]: Using backend ThreadingBackend with 2 concurrent workers.
[Parallel(n_jobs=2)]: Done  46 tasks      | elapsed:    0.0s
[Parallel(n_jobs=2)]: Done 100 out of 100 | elapsed:    0.0s finished
/usr/local/lib/python3.10/dist-packages/sklearn/ensemble/_forest.py:400: FutureWarning: Criterion 'mse' was deprecated in v1.0 and will be removed in version 1.2. Use `criterion='squared_error'` which is equivalent.
  warn(
/usr/local/lib/python3.10/dist-packages/sklearn/ensemble/_forest.py:416: FutureWarning: `max_features='auto'` has been deprecated in 1.1 and will be removed in 1.3. To keep the past behaviour, explicitly set `max_features=1.0` or remove this parameter as it is also the default value for RandomForestRegressors and ExtraTreesRegressors.
  warn(
[Parallel(n_jobs=-1)]: Using backend ThreadingBackend with 2 concurrent workers.
[Parallel(n_jobs=-1)]: Done  46 tasks      | elapsed:    0.1s
[Paral

...

[Parallel(n_jobs=-1)]: Done  46 tasks      | elapsed:    0.1s
[Parallel(n_jobs=-1)]: Done 100 out of 100 | elapsed:    0.3s finished
[Parallel(n_jobs=2)]: Using backend ThreadingBackend with 2 concurrent workers.
[Parallel(n_jobs=2)]: Done  46 tasks      | elapsed:    0.0s
[Parallel(n_jobs=2)]: Done 100 out of 100 | elapsed:    0.0s finished
/usr/local/lib/python3.10/dist-packages/sklearn/ensemble/_forest.py:400: FutureWarning: Criterion 'mse' was deprecated in v1.0 and will be removed in version 1.2. Use `criterion='squared_error'` which is equivalent.
  warn(
/usr/local/lib/python3.10/dist-packages/sklearn/ensemble/_forest.py:416: FutureWarning: `max_features='auto'` has been deprecated in 1.1 and will be removed in 1.3. To keep the past behaviour, explicitly set `max_features=1.0` or remove this parameter as it is also the default value for RandomForestRegressors and ExtraTreesRegressors.
  warn(
[Parallel(n_jobs=-1)]: Using backend ThreadingBackend with 2 concurrent workers.
[Paral

Iteration: 1


[Parallel(n_jobs=-1)]: Done 100 out of 100 | elapsed:    0.3s finished
[Parallel(n_jobs=2)]: Using backend ThreadingBackend with 2 concurrent workers.
[Parallel(n_jobs=2)]: Done  46 tasks      | elapsed:    0.0s
[Parallel(n_jobs=2)]: Done 100 out of 100 | elapsed:    0.0s finished
/usr/local/lib/python3.10/dist-packages/sklearn/ensemble/_forest.py:400: FutureWarning: Criterion 'mse' was deprecated in v1.0 and will be removed in version 1.2. Use `criterion='squared_error'` which is equivalent.
  warn(
/usr/local/lib/python3.10/dist-packages/sklearn/ensemble/_forest.py:416: FutureWarning: `max_features='auto'` has been deprecated in 1.1 and will be removed in 1.3. To keep the past behaviour, explicitly set `max_features=1.0` or remove this parameter as it is also the default value for RandomForestRegressors and ExtraTreesRegressors.
  warn(
[Parallel(n_jobs=-1)]: Using backend ThreadingBackend with 2 concurrent workers.
[Parallel(n_jobs=-1)]: Done  46 tasks      | elapsed:    0.1s
[Paral

Iteration: 2


[Parallel(n_jobs=-1)]: Done  46 tasks      | elapsed:    0.1s
[Parallel(n_jobs=-1)]: Done 100 out of 100 | elapsed:    0.1s finished
[Parallel(n_jobs=2)]: Using backend ThreadingBackend with 2 concurrent workers.
[Parallel(n_jobs=2)]: Done  46 tasks      | elapsed:    0.0s
[Parallel(n_jobs=2)]: Done 100 out of 100 | elapsed:    0.0s finished


In [ ]:
mse_MF

[536.4201948262548,
 510.06638054054054,
 506.32936528957526,
 575.6054297683398,
 508.3511871042471,
 508.90323594594594,
 498.4239019691119,
 517.6187637451736,
 599.7432614285715,
 578.9852338223939,
 519.2563548648649,
 499.07197185328187,
 514.8091548648649,
 536.6582647104248,
 516.5960963706564,
 499.94126722007724,
 517.9189923166024,
 510.1581851737452,
 605.3112096911196,
 517.6942946332047,
 549.7645363320463,
 574.2049705019306,
 559.5984911583013,
 551.0680838223938,
 555.2812898069499,
 520.4294019691121,
 537.2666469498068,
 559.9092247490348,
 516.9967183783783,
 515.3672015830117,
 556.699336911197,
 545.7532195366795,
 577.658506023166,
 516.6234986872587,
 581.3161216602316,
 511.12527301158303,
 504.7773797683398,
 523.9977334362935,
 515.9664235907336,
 517.1976500386099,
 594.4450753281853,
 512.8536917374518,
 562.6863266795366,
 532.040339034749,
 532.3799855598455,
 576.9799465637066,
 534.9086535135135,
 578.1457241698841,
 548.7608355598455,
 523.555167992278

**SimpleImpute**
```
* Mode = If the data type is 'object'.
* Mean = If the data type is numeric (not 'object') and dont have outlier
* Median = If the data type is numeric (not 'object') and have outlier
```

In [ ]:
df = widetable.copy()

In [ ]:
# Repeat similar process for Simple Impute
columns_to_keep = ['PatientUID', 'PatientVisitUID', 'Slopes', 'InPatient', 'OutPatient', 'Emergency', 'eGFR_t1','time_t1', 'VisitLocation', 'StartDTTM', 'EndDttm', 'LabCwhen']
df_subset = df.loc[df_with_missing.index]
missing_for_binary = pd.concat([df_subset[columns_to_keep], df_with_missing], axis=1)

for column in df_with_missing.columns:
    missing_for_binary.loc[random_missing_indices[column], column] = np.nan

def detect_outliers(data, column):
    q1 = data[column].quantile(0.25)
    q3 = data[column].quantile(0.75)
    iqr = q3 - q1
    lower_bound = q1 - 1.5 * iqr
    upper_bound = q3 + 1.5 * iqr
    outliers = data[(data[column] < lower_bound) | (data[column] > upper_bound)]
    return not outliers.empty

columns_with_null = missing_for_binary.columns[missing_for_binary.isnull().any()].tolist()
imputed_table = missing_for_binary.copy()

In [ ]:
def fill_missing_values(data, column, method):
    if method == 'mean':
        data[column].fillna(data[column].mean(), inplace=True)
    elif method == 'median':
        data[column].fillna(data[column].median(), inplace=True)
    elif method == 'mode':
        data[column].fillna(data[column].mode()[0], inplace=True)
    imputed_table = df_with_missing.copy()

In [ ]:
num_iterations = 50

mse_simple = []
mae_simple = []
mape_simple = []

for _ in range(num_iterations):
    # Move the generation of random missing indices inside the loop
    random_missing_indices = {}
    for column in df_with_missing.columns:
        num_missing = int(np.round(missing_probabilities[column] * len(df_with_missing)))
        random_missing_indices[column] = np.random.choice(len(df_with_missing), num_missing, replace=False)

    imputed_table = missing_for_binary.copy()  # Make sure to copy the DataFrame

    for column in columns_with_null:
        if column in imputed_table.select_dtypes(include=['object']).columns:
            # Fill null values with a randomly chosen mode value for object columns
            mode_values = imputed_table[column].mode()
            imputed_table.loc[random_missing_indices[column], column] = np.random.choice(mode_values)
        elif column in imputed_table.select_dtypes(include=['float64']).columns:
            if detect_outliers(df_subset, column):
                # Median imputation for numeric columns with outliers
                median_values = df_subset.groupby('PatientVisitUID')[column].median()
                imputed_table.loc[random_missing_indices[column], column] = imputed_table.loc[random_missing_indices[column], 'PatientVisitUID'].map(median_values)
            else:
                # Mean imputation for numeric columns without outliers
                mean_values = df_subset.groupby('PatientVisitUID')[column].mean()
                imputed_table.loc[random_missing_indices[column], column] = imputed_table.loc[random_missing_indices[column], 'PatientVisitUID'].map(mean_values)

    # Check for outliers in each column and fill missing values accordingly
    for column in columns_with_null:
        outliers = detect_outliers(imputed_table, column)
        if imputed_table[column].dtype == 'object':
            imputed_table[column].fillna(imputed_table[column].mode()[0], inplace=True)
        elif not outliers:
            imputed_table[column].fillna(imputed_table[column].mean(), inplace=True)
        else:
            imputed_table[column].fillna(imputed_table[column].median(), inplace=True)

    # Drop columns if needed
    imputed_table = imputed_table.drop(columns=columns_to_keep)

    # Calculate and append results
    mse_simple.append(mean_squared_error(no_missing, imputed_table))
    true_values_simple = no_missing.values.flatten()
    imputed_values_simple = imputed_table.values.flatten()

    non_zero_mask_simple = true_values_simple != 0
    true_values_non_zero_simple = true_values_simple[non_zero_mask_simple]
    imputed_values_non_zero_simple = imputed_values_simple[non_zero_mask_simple]

    mape_simple.append(np.mean(np.abs((true_values_non_zero_simple - imputed_values_non_zero_simple) / true_values_non_zero_simple)) * 100)
    mae_simple.append(mean_absolute_error(no_missing, imputed_table))


In [ ]:
mape_simple

[9.070307814428649,
 9.666508037671322,
 13.007205232351444,
 13.258576730097671,
 10.34063131445319,
 9.9644718800614,
 8.863910847430104,
 11.28379976258249,
 13.331790974540525,
 10.253964530006865,
 9.410324712739897,
 9.869294692795828,
 9.734013847386516,
 10.271691364598196,
 12.52988368723575,
 10.358084321192806,
 9.583501980494297,
 10.21086126357308,
 10.326387421597062,
 13.209478177929471,
 9.8032710455606,
 10.2730567106396,
 10.483699756395154,
 9.33015416626175,
 13.351582797220448,
 9.834494370393543,
 10.092512194801907,
 10.119773014878048,
 10.381215374478824,
 9.339675015695981,
 10.457082022618314,
 10.384074649962459,
 10.287856490595907,
 10.534628394172094,
 16.539786079242766,
 13.440414679803926,
 9.574196182120318,
 10.48743601530793,
 10.23942841424572,
 10.214876167660641,
 10.21912519994464,
 10.280938119088894,
 10.334189085473927,
 10.502527459806899,
 10.107410126320982,
 10.022950059509519,
 11.207184636138548,
 9.481772578827261,
 9.997703550598022,


#**Compare**



In [ ]:
import pandas as pd
import numpy as np

# Assuming you have the following results:
mae_results = {'MF': mae_MF, 'Mice': mae_Mice, 'Simple': mae_simple}
mse_results = {'MF': mse_MF, 'Mice': mse_Mice, 'Simple': mse_simple}
mape_results = {'MF': mape_MF, 'Mice': mape_Mice, 'Simple': mape_simple}

# Calculate means of the results
mean_mse_results = {method: np.mean(results) for method, results in mse_results.items()}
mean_mape_results = {method: np.mean(results) for method, results in mape_results.items()}
mean_mae_results = {method: np.mean(results) for method, results in mae_results.items()}

# Convert means to a DataFrame for easier printing
mean_evaluation_df = pd.DataFrame({
    'Method': list(mean_mse_results.keys()),
    'Mean MSE': list(mean_mse_results.values()),
    'Mean MAPE': list(mean_mape_results.values()),
    'Mean MAE': list(mean_mae_results.values())
})

mean_evaluation_df


Method    Mean MSE  Mean MAPE  Mean MAE
0      MF  537.312404  10.387709  2.804269
1    Mice  557.111982  12.446803  3.039901
2  Simple  552.057365  10.699246  2.957992

In [ ]:
import matplotlib.pyplot as plt
from sklearn.metrics import mean_squared_error, mean_absolute_error

imputed_data = {'OriginalData': no_missing}
imputed_data['Mice'] = Mice
imputed_data['MissForest'] = MissForest
imputed_data['SimpleImpute'] = imputed_table